### Librerias Utilizadas

In [1]:
import mne
import numpy as np
import matplotlib.pyplot as plt
import scipy.signal
from scipy.signal import stft, get_window
from scipy.stats import entropy
import os
import pickle

# Funciones

 Cargar el archivo .set y obtener los datos. 

In [2]:
def cargar_eeg(filepath):
    raw = mne.io.read_raw_eeglab(filepath, preload=True)
    return raw


Si se ha eliminado algún canal por contener artefactos en el preprocesamiento, se aplica esta función que calcula la media de los canales en ese archivo y los añade para tener 62. 

In [47]:
def add_channels(raw, target_n_channels=62):
    n_channels = len(raw.ch_names)
    if n_channels < target_n_channels:
        mean_channel = np.mean(raw.get_data(), axis=0)
        for i in range(n_channels + 1, target_n_channels + 1):
            ch_name = f'EEG {i}'
            info = mne.create_info(ch_names=[ch_name], sfreq=raw.info['sfreq'], ch_types='eeg')
            new_raw = mne.io.RawArray(mean_channel[np.newaxis, :], info)
            raw.add_channels([new_raw], force_update_info=True)

Calcular la Entropía Diferencial (DE) a partir de la Transformada de Fourier de Tiempo Corto (STFT) en diferentes bandas de frecuencia para la señal EEG.

In [48]:
# Define frequency bands
bands = {
    'delta': (1, 4),
    'theta': (4, 8),
    'alpha': (8, 14),
    'beta': (14, 31),
    'gamma': (31, 50)
}

# Compute Differential Entropy from STFT
def compute_de_from_stft(segment, fs=400):
    window_size = int(fs * 1)  # window size of 1 second
    de_features = []
    for band, (low, high) in bands.items():
        # Compute the STFT with a Hanning window
        f, t, Zxx = scipy.signal.stft(segment, fs=fs, window='hann', nperseg=window_size, noverlap=0)
        band_indices = np.where((f >= low) & (f <= high))[0]
        if len(band_indices) == 0:
            continue
        
        band_power = np.abs(Zxx[band_indices, :])**2
        band_power_mean = np.mean(band_power)
        de = 0.5 * np.log(2 * np.pi * np.e * band_power_mean)
        de_features.append(de)
    return np.array(de_features).flatten()

# FEATURE EXTRACTION

Se procesan los archivos EEG en formato .set generados en el preproceso para extraer características de entropía diferencial usando la Transformada de Fourier de Tiempo Corto (STFT). Para cada archivo .set en el directorio de entrada, se cargan los datos y se añaden canales si es necesario. Se dividen los datos en épocas de 4 segundos sin solapamiento. Luego, para cada canal dentro de cada época, se calcula la DE con la función definida anteriormente. Las características de todas las épocas se concatenan en una matriz se que se guarda en un archivo .pkl. Se imprimen las dimensiones del array de características y los primeros resultados procesados. 

In [50]:
input_dir = '.../0.EEG_preprocessed'
output_dir = '.../1.EEG_features'


# Listar todos los archivos .set en el directorio de entrada
for filename in os.listdir(input_dir):
    if filename.endswith('.set'):
        file_path = os.path.join(input_dir, filename)
        raw = cargar_eeg(file_path)
        add_channels(raw)

        duration = 4
        epochs = mne.make_fixed_length_epochs(raw, duration=duration, preload=True, overlap=0)
        all_de_features = []

        for epoch_data in epochs.get_data():
            epoch_features = []
            for channel_data in epoch_data:
                de_features = compute_de_from_stft(channel_data, fs=raw.info['sfreq'])
                epoch_features.append(de_features)
            all_de_features.append(np.concatenate(epoch_features))

        all_de_features = np.array(all_de_features)

        # Guardar las características en un archivo
        output_file_path = os.path.join(output_dir, filename.replace('.set', '_features.pkl'))
        with open(output_file_path, 'wb') as f:
            pickle.dump(all_de_features, f)

        # Imprimir las dimensiones y un head de las primeras tres filas
        print(f"Processed {filename}: features saved to {output_file_path}")
        print("Shape of the features array:", all_de_features.shape)
        print(all_de_features[:1])

Not setting metadata
35 matching events found
No baseline correction applied
0 projection items activated
Using data from preloaded Raw for 35 events and 1600 original time points ...
0 bad epochs dropped


C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: Limited 2 annotation(s) that were expanding outside the data range.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)
C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: The data contains 'boundary' events, indicating data discontinuities. Be cautious of filtering and epoching around these events.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)


Processed 10_1_10_preprocessed.set: features saved to C:/Users/pablo/OneDrive/Escritorio/UPV/TFG/SEED V/EEGLAB/1.EEG_features\10_1_10_preprocessed_features.pkl
Shape of the features array: (35, 310)
First 3 rows of features:
[[-11.30731198 -12.11530695 -12.70477923 -13.32959461 -13.78427351
  -11.33189977 -12.12165697 -12.80634473 -13.41319931 -13.86657634
  -11.27421856 -12.05181641 -12.809263   -13.3486485  -13.68538778
  -11.79523878 -12.55996387 -12.94367212 -13.63688319 -14.06566055
  -11.75288605 -12.46723998 -13.05660506 -13.62207053 -13.74334524
  -11.93899356 -12.70774581 -12.89372487 -13.40821031 -13.63671589
  -12.07336344 -12.94812512 -12.99716528 -12.96515232 -12.81521633
  -12.26311492 -13.10322777 -13.20016833 -13.58445391 -13.71107913
  -12.25325237 -13.09858788 -13.08457194 -13.93757574 -14.36092939
  -12.37363544 -13.00172041 -13.01045997 -13.87121715 -14.25163796
  -12.39816392 -13.10077149 -13.1455421  -14.03091727 -14.07000837
  -12.4287226  -13.04600366 -13.255478

C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: Limited 2 annotation(s) that were expanding outside the data range.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)
C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: The data contains 'boundary' events, indicating data discontinuities. Be cautious of filtering and epoching around these events.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)


Processed 10_1_11_preprocessed.set: features saved to C:/Users/pablo/OneDrive/Escritorio/UPV/TFG/SEED V/EEGLAB/1.EEG_features\10_1_11_preprocessed_features.pkl
Shape of the features array: (43, 310)
First 3 rows of features:
[[-10.04592476 -10.8418026  -11.74343662 -12.85921678 -13.19500279
  -10.07789156 -10.87760711 -11.7033806  -13.02197784 -13.48138598
  -10.02256476 -10.83406641 -11.68171857 -12.90162879 -12.84121851
  -10.57594366 -11.39001391 -12.12383649 -13.18909263 -13.86916612
  -10.57190161 -11.44728163 -12.05739926 -12.99557582 -13.28867704
  -11.18920402 -12.23352306 -12.72324328 -12.94255468 -13.36186772
  -11.238211   -12.28944673 -12.76318696 -13.35769113 -13.79621186
  -11.38688582 -12.19343778 -12.69647043 -13.43677636 -14.20623162
  -11.32305649 -12.22132813 -12.59434088 -13.40166822 -14.26038506
  -11.2237753  -12.26153481 -12.46026781 -13.39804861 -14.22391158
  -11.20944416 -12.23067012 -12.46489218 -13.40824772 -14.0533252
  -11.17296233 -12.16502099 -12.5397815

...

Processed 9_3_7_preprocessed.set: features saved to C:/Users/pablo/OneDrive/Escritorio/UPV/TFG/SEED V/EEGLAB/1.EEG_features\9_3_7_preprocessed_features.pkl
Shape of the features array: (21, 310)
First 3 rows of features:
[[ -9.86132155 -10.44212658 -11.41941083 -12.3481092  -12.56903229
   -9.80946831 -10.40346855 -11.3907071  -12.31419072 -12.65651236
   -9.80148927 -10.39030978 -11.40858555 -12.34426522 -12.76749118
  -10.49223806 -11.06560751 -12.03137109 -12.87953007 -13.40974391
  -10.37072014 -10.94184133 -11.96184498 -12.86004653 -13.26206065
  -10.94935735 -11.96225909 -12.60294074 -12.95200831 -13.31777585
  -10.89373503 -11.72922062 -12.48078423 -13.0115023  -13.38958944
  -11.41294097 -11.96659244 -12.74787735 -13.25276563 -13.8377447
  -11.47214905 -11.90770433 -12.75045816 -13.37415637 -13.98975525
  -11.54851554 -11.91526965 -12.78434315 -13.4461383  -13.97156898
  -11.39391329 -11.80339515 -12.72065911 -13.41984339 -13.93605056
  -11.08555815 -11.59925991 -12.55122533 -1

C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: Limited 2 annotation(s) that were expanding outside the data range.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)
C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: The data contains 'boundary' events, indicating data discontinuities. Be cautious of filtering and epoching around these events.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)


Processed 9_3_8_preprocessed.set: features saved to C:/Users/pablo/OneDrive/Escritorio/UPV/TFG/SEED V/EEGLAB/1.EEG_features\9_3_8_preprocessed_features.pkl
Shape of the features array: (18, 310)
First 3 rows of features:
[[ -9.58464241 -10.10008695 -10.98781275 -11.96306093 -12.46019076
   -9.56695733 -10.06526248 -10.99120926 -11.99915983 -12.50485699
   -9.52612375 -10.05076696 -10.99813205 -11.96215816 -12.49180302
  -10.19483259 -10.7257283  -11.60225025 -12.40287859 -12.9860632
  -10.11090216 -10.62666187 -11.54162979 -12.52845861 -13.06617407
  -10.47955362 -11.4070863  -12.08783681 -12.5876255  -13.06621417
  -10.52777146 -11.2614923  -12.00190663 -12.63591658 -13.20857608
  -10.96253911 -11.56062815 -12.34064587 -12.87497327 -13.40651401
  -11.09874527 -11.57280131 -12.41377708 -13.09241116 -13.80682509
  -11.31151767 -11.69187971 -12.54196527 -13.23750062 -14.02311811
  -11.10945416 -11.53619495 -12.37977314 -13.19273935 -13.87317465
  -10.75941868 -11.28545891 -12.10161693 -1

C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: Limited 2 annotation(s) that were expanding outside the data range.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)
C:\Users\pablo\AppData\Local\Temp\ipykernel_16756\2968136323.py:3: RuntimeWarning: The data contains 'boundary' events, indicating data discontinuities. Be cautious of filtering and epoching around these events.
  raw = mne.io.read_raw_eeglab(filepath, preload=True)


Processed 9_3_9_preprocessed.set: features saved to C:/Users/pablo/OneDrive/Escritorio/UPV/TFG/SEED V/EEGLAB/1.EEG_features\9_3_9_preprocessed_features.pkl
Shape of the features array: (57, 310)
First 3 rows of features:
[[ -9.61180268 -10.52492666 -11.55876007 -12.4163621  -12.81677075
  -10.24196104 -11.15466097 -12.07017231 -13.16471891 -13.47324543
  -10.14888849 -11.10250283 -12.04632829 -12.82986766 -13.35293603
  -10.66888251 -11.87969184 -12.4026821  -13.16040485 -13.53496413
  -10.69844853 -11.69770772 -12.38636653 -13.1782261  -13.4068608
  -10.98176977 -12.03107607 -12.68221007 -13.48217281 -13.95276159
  -10.9924495  -12.00205361 -12.75989606 -13.5563795  -14.03032378
  -11.15854616 -12.06714781 -12.8041938  -13.51642339 -13.96434684
  -10.98972171 -11.99386799 -12.64622647 -13.32782069 -13.8933949
  -10.74437549 -11.79758649 -12.43168781 -12.983734   -13.56007575
  -10.59032829 -11.67725721 -12.40985225 -12.45717221 -12.62979232
  -10.31339391 -11.41115133 -12.31214452 -12

# AÑADIR ETIQUETAS

Se añaden las etiquetas en función del numero de sesión y el número de experimento. Hay un archivo .xls proporcionado con los datos del SEED-V que indica que etiqueta está asociada a cada video en cada sesión. 

In [51]:
# Definir el diccionario de etiquetas basado en la sesión y el trial
labels = {
    1: ['Happy', 'Fear', 'Neutral', 'Sad', 'Disgust', 'Happy', 'Fear', 'Neutral', 'Sad', 'Disgust', 'Happy', 'Fear', 'Neutral', 'Sad', 'Disgust'],
    2: ['Sad', 'Fear', 'Neutral', 'Disgust', 'Happy', 'Happy', 'Disgust', 'Neutral', 'Sad', 'Fear', 'Neutral', 'Happy', 'Fear', 'Sad', 'Disgust'],
    3: ['Sad', 'Fear', 'Neutral', 'Disgust', 'Happy', 'Happy', 'Disgust', 'Neutral', 'Sad', 'Fear', 'Neutral', 'Happy', 'Fear', 'Sad', 'Disgust']
}

# Rutas de los archivos
ruta_archivos = r'...\1.EEG_features'
ruta_guardado = r'...\2.EEG_labels'

# Crear la ruta de guardado si no existe
os.makedirs(ruta_guardado, exist_ok=True)

# Función para procesar los archivos
def agregar_etiqueta_a_archivos(ruta_lectura, ruta_escritura):
    for archivo in os.listdir(ruta_lectura):
        if archivo.endswith('.pkl'):
            # Extraer números de sesión y trial del nombre del archivo
            partes = archivo.split('_')
            if len(partes) >= 4:
                sesion = int(partes[1])  # Asumiendo que el segundo elemento es la sesión
                trial = int(partes[2])  # Asumiendo que el tercer elemento es el trial
                
                # Cargar el archivo .pkl
                with open(os.path.join(ruta_lectura, archivo), 'rb') as f:
                    data = pickle.load(f)
                
                # Obtener la etiqueta correspondiente
                etiqueta = labels[sesion][trial - 1]
                
                # Crear una columna de etiquetas
                etiqueta_columna = np.full((data.shape[0], 1), etiqueta, dtype=object)
                
                # Concatenar la columna de etiquetas al array de datos
                data_con_etiqueta = np.hstack((data, etiqueta_columna))
                
                # Guardar el nuevo archivo con la etiqueta añadida
                nuevo_nombre_archivo = os.path.join(ruta_escritura, archivo)
                with open(nuevo_nombre_archivo, 'wb') as f:
                    pickle.dump(data_con_etiqueta, f)
                print(f"Archivo procesado y guardado: {nuevo_nombre_archivo}")

# Ejecutar la función
agregar_etiqueta_a_archivos(ruta_archivos, ruta_guardado)

Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_10_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_11_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_12_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_13_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_14_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_15_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\2.EEG_labels\10_1_1_preprocessed_features.pkl
Archivo procesado y guardado: C:\Users\pablo\OneDrive\Escritori

# CONCATENAR Y EXPORTAR CSV

Para cada archivo, carga los datos, reemplaza las etiquetas categóricas por sus correspondientes valores numéricos, y luego los concatena en un único DataFrame que se guarda como CSV.

In [61]:
#ETIQUETAS A NUMERICO Y CONCATENAR

# Ruta de entrada de los archivos
ruta_entrada = r'...\2.EEG_labels'

# Ruta de salida para el archivo combinado
ruta_salida = r'...\3.EEG_concat\concatenated_features.csv'

# Asegurar que el directorio de salida existe
os.makedirs(os.path.dirname(ruta_salida), exist_ok=True)

# Diccionario de mapeo de etiquetas
label_mapping = {
    'Disgust': 0,
    'Fear': 1,
    'Sad': 2,
    'Neutral': 3,
    'Happy': 4
}

def procesar_archivos_y_combinar(ruta_entrada):
    dataframes = []
    
    for archivo in os.listdir(ruta_entrada):
        if archivo.endswith('.pkl'):
            ruta_completa = os.path.join(ruta_entrada, archivo)
            with open(ruta_completa, 'rb') as f:
                data = pickle.load(f)
            
            # Asumimos que las etiquetas están en la última columna
            etiquetas_numericas = np.vectorize(label_mapping.get)(data[:, -1].astype(str))
            
            # Reemplazamos la última columna con las nuevas etiquetas numéricas
            data[:, -1] = etiquetas_numericas
            
            # Convertimos el array a DataFrame
            df = pd.DataFrame(data)
            dataframes.append(df)
    
    # Combinar todos los DataFrames en uno solo
    df_combinado = pd.concat(dataframes, ignore_index=True)
    
    # Renombrar la última columna a 'Label'
    df_combinado.rename(columns={df_combinado.columns[-1]: 'Label'}, inplace=True)
    
    return df_combinado

# Llamar a la función y obtener el DataFrame combinado
df_final = procesar_archivos_y_combinar(ruta_entrada)

# Guardar el DataFrame final como CSV
df_final.to_csv(ruta_salida, index=False)

print("DataFrame combinado guardado en:", ruta_salida)


DataFrame combinado guardado exitosamente en: C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\3.EEG_concat\concatenated_features.csv


In [62]:
#COMPROBACION CSV

# Ruta al archivo CSV generado
ruta_csv = r'C:\Users\pablo\OneDrive\Escritorio\UPV\TFG\SEED V\EEGLAB\3.EEG_concat\concatenated_features.csv'

# Cargar el CSV en un DataFrame
df = pd.read_csv(ruta_csv)

# Obtener las dimensiones del DataFrame
dimensiones = df.shape
print("Dimensiones del DataFrame:", dimensiones)

# Obtener valores únicos de la última columna (asumimos que se llama 'Label')
valores_unicos = df['Label'].unique()
print("Valores únicos en la última columna 'Label':", valores_unicos)

Dimensiones del DataFrame: (29168, 311)
Valores únicos en la última columna 'Label': [0 4 1 3 2]


In [68]:
df.head()

0          1          2          3          4          5  \
0 -11.307312 -12.115307 -12.704779 -13.329595 -13.784274 -11.331900   
1 -11.689588 -12.594864 -12.673640 -13.357145 -13.638857 -11.599017   
2 -10.299438 -11.387675 -12.479711 -13.260607 -13.748846 -10.303433   
3 -10.665919 -11.939164 -12.607145 -13.308256 -13.589286 -10.761043   
4 -10.643628 -11.496307 -12.369233 -13.337486 -13.750320 -10.611664   

           6          7          8          9  ...        301        302  \
0 -12.121657 -12.806345 -13.413199 -13.866576  ... -13.215460 -13.255321   
1 -12.559218 -12.692139 -13.435648 -13.716502  ... -13.032858 -13.003571   
2 -11.395273 -12.559843 -13.350619 -13.815496  ... -12.415856 -13.301192   
3 -12.010136 -12.646603 -13.384258 -13.650757  ... -13.089747 -13.212368   
4 -11.512877 -12.368836 -13.343951 -13.815115  ... -12.792912 -13.059322   

         303        304        305        306        307        308  \
0 -13.958622 -14.402749 -11.010244 -12.067960 -12.188378 -12.495591   
1 -13.672386 -14.407889 -10.097439 -11.088616 -11.637666 -12.190241   
2 -13.810145 -14.393727 -10.977846 -11.835514 -12.297537 -12.518452   
3 -13.803853 -14.466754 -10.697992 -12.007851 -12.059200 -12.676292   
4 -13.808845 -14.538038 -11.107099 -11.981999 -12.052780 -12.561383   

         309  Label  
0 -12.717701      0  
1 -12.605762      0  
2 -12.734836      0  
3 -12.805461      0  
4 -12.748687      0  

[5 rows x 311 columns]